## R Shiny Dashboard Resources

1) Structure overview of R Shiny: https://rstudio.github.io/shinydashboard/structure.html

2) Interface Component example code: https://shiny.rstudio.com/gallery/dynamic-ui.html

3) Flex Dashboard layout ref: https://rmarkdown.rstudio.com/flexdashboard/

4) Flex Dashboard gallery: https://rmarkdown.rstudio.com/flexdashboard/examples.html

5) Shiny Dashboard gallery: https://rstudio.github.io/shinydashboard/examples.html

6) Mapping in R: https://bookdown.org/robinlovelace/geocompr/adv-map.html

7) Integrating Leaflet and dygraphy [THIS IS WHAT I WANT TO DO!]: https://stackoverflow.com/questions/31814037/integrating-time-series-graphs-and-leaflet-maps-using-r-shiny

## Import Libraries and Cleaned Datasets

In [4]:
## Install missing R libraries for the renvironment programming env
#     install.packages("shinydashboard")
#     install.packages("leaflet")
#     install.packages("curl")
#     install.packages("shiny")
#     install.packages('htmltools')
#     install.packages('dygraphs')
#     install.packages("RSpectra")
#     install.packages('geojsonR')
#     install.packages("devtools")
#     install.packages("leaflet",dependencies = T) ## Update Pkgs if not installing properly
#     install.packages("leaflet.extras",dependencies = T)
#     install.packages("proj4")
#     install.packages("leaflethex")
#     install.packages('IRkernel')
#     devtools::install_github("rpruim/leaflethex")


# devtools::install_github("ropensci/geojsonio")
# install.packages("rgeos", type = "source")

# update.packages(ask = FALSE, checkBuilt = TRUE)
# R.Version() # version 3.6.1
getwd()

[1] "/home/hp-nunes/dev/repo/R_dataViz"

In [2]:
library(rgdal)
library(plyr)
library(dplyr)
library(ggplot2)
library(geojsonR)
library(shinydashboard)
library(curl) # make the jsonlite suggested dependency explicit
library(shiny)
library(htmlwidgets)
library(IRdisplay)
library(dygraphs)
library(devtools)
# library(RSpectra)
library(leaflet)
library(leaflet.extras)
library(RColorBrewer)
library(rgeos)
library(tibble)
library(leaflethex)
library(rgeos)
## library(geojsonio) # Failed installation in the IPython Kernel; works in RStudio.

Updating R in the Jupyter Conda environment: http://salvatoregiorgi.com/blog/2018/10/16/installing-an-older-version-of-r-in-a-conda-environment/

In [ ]:
devtools::session_info()

### Installing rgdal: a pain in the a*&$%$%$ !

* Installing rgdal via the console: https://stackoverflow.com/questions/56445865/install-rgdal-on-ubuntu-18-04
* Do I need to locate the pkg to finalize installation: https://community.rstudio.com/t/a-few-r-packages-are-installed-in-a-tmp-library-but-i-they-cant-be-found-using-library-package/16408
* SOLUTION: https://github.com/conda-forge/r-rgdal-feedstock/issues/18
* Useful ref: https://rtask.thinkr.fr/installation-of-r-3-5-on-ubuntu-18-04-lts-and-tips-for-spatial-packages/
* Workaround w/problems installing r-pkgs: https://www.haktansuren.com/installing-r-package-fixing-package-xxx-is-not-available-for-r-version-x-y-z-warning/

## Importing Datasets

In [6]:
airNow <- read.csv("assets/AirNowdata2020.csv")
purpleAir <- read.csv("assets/purpleAirdata2020.csv")

nrow(purpleAir)
nrow(airNow)

colnames(purpleAir)
colnames(airNow)

[1] 343779

[1] 2349

[1] "dateTime"         "Humidity_."       "PM1.0_CF1_ug.m3"  "PM10.0_CF1_ug.m3"
 [5] "PM2.5_ATM_ug.m3"  "PM2.5_CF1_ug.m3"  "Pressure_hpa"     "RSSI_dbm"        
 [9] "Temperature_F"    "UptimeMinutes"    "location"         "Longitude"       
[13] "Latitude"         "location_type"    "date"             "hour"

[1] "dateTime"    "date"        "parameter"   "location"    "value"      
 [6] "unit"        "city"        "attribution" "hour"        "Latitude"   
[11] "Longitude"

In [7]:
# Group purpleAir by unique location (mapping)
purpleAir2 <- read.csv("assets/purpleAir_byUniqueLocations.csv")
nrow(purpleAir2)
colnames(purpleAir2)

# Timeseries Dataset
purpleAirT <- read.csv("assets/purpleAir_TimeseriesDataset.csv")
nrow(purpleAirT)
colnames(purpleAirT)

# Importing the spatial dataset as shapefiles
vulnerability <- readOGR(dsn="assets/shp/", layer="vulnerability")
baaqmdSF <- readOGR(dsn="assets/shp/", layer="baaqmdSF")

[1] 105

[1] "X"                 "Latitude"          "Longitude"        
 [4] "location"          "location_type"     "day_count"        
 [7] "measurement_count" "Humidity_."        "PM2.5_ATM_ug.m3"  
[10] "Temperature_F"     "UptimeMinutes"     "PM10.0_CF1_ug.m3" 
[13] "PM1.0_CF1_ug.m3"   "PM2.5_CF1_ug.m3"

[1] 10738

[1] "Latitude"         "Longitude"        "location"         "location_type"   
 [5] "dateTime"         "Humidity_."       "PM1.0_CF1_ug.m3"  "PM10.0_CF1_ug.m3"
 [9] "PM2.5_ATM_ug.m3"  "PM2.5_CF1_ug.m3"  "Pressure_hpa"     "RSSI_dbm"        
[13] "Temperature_F"    "UptimeMinutes"    "Longitude.1"      "Latitude.1"

OGR data source with driver: ESRI Shapefile 
Source: "/home/hp-nunes/dev/repo/R_dataViz/assets/shp", layer: "vulnerability"
with 1 features
It has 1 fields
OGR data source with driver: ESRI Shapefile 
Source: "/home/hp-nunes/dev/repo/R_dataViz/assets/shp", layer: "baaqmdSF"
with 117 features
It has 3 fields


## Mapping

* Following this tutorial: https://medium.com/@joyplumeri/how-to-make-interactive-maps-in-r-shiny-brief-tutorial-c2e1ef0447da

### Having some trouble loading GEOJSON...but I found a workaround importing shp. Example below:

ref: http://zevross.com/blog/2016/01/13/tips-for-reading-spatial-files-into-r-with-rgdal/

In [ ]:
## Import spatial dataset as GEOJSON (NOT WORKING)
# geojson <- jsonlite::fromJSON("assets/openSF_vulnerablePops.geojson")
# baaqmd = FROM_GeoJson(url_file_string = "assets/openSF_baaqmd.geojson")

## using rshiny to publish the map
ui <- leaflet() %>% 
  addTiles() %>%
  setView(lng = -122.3978, lat = 37.7658, zoom = 12) %>% 
  addPolygons(data = res)


server <- function(input, output, session) {

}

shinyApp(ui, server)

### Choropleths

choropleth tutorial: 

1) https://learn.r-journalism.com/en/mapping/census_maps/census-maps/

2) https://www.r-graph-gallery.com/183-choropleth-map-with-leaflet.html

In [11]:
m = leaflet(vulnerability) %>%
    addProviderTiles(providers$CartoDB.Positron) %>%
    setView(-122.3978, 37.7658, zoom = 12) %>%
  addPolygons(color = "#444444", weight = 1, smoothFactor = 0.5,
    opacity = 1.0, fillOpacity = 0.5,
    highlightOptions = highlightOptions(color = "white", weight = 2,
      bringToFront = TRUE))
# * Uncomment
htmlwidgets::saveWidget(m, "m.html")
# * Uncomment
rawHTML = base64enc::dataURI(mime = "text/html;charset=utf-8", file = "m.html")
display_html(paste("<iframe src=", rawHTML, "width=100% height=450></iframe>", sep = "\""))
unlink("m.html")

In [12]:
## Choropleth of BAAQMD's PM2.5 measurements (OpenDataSF)

mybins <- c(8.08,8.37,8.54,8.81,9.19,9.43)
pal <- colorBin( palette="Reds", domain=baaqmdSF$PM25, na.color="transparent", bins=mybins)

popup_sb <- paste0("<strong>Neighborhood: ", baaqmdSF$name)

# Prepare the text for tooltips:
mytext <- paste(
    "<strong>PM2.5 (µg/m³): ", baaqmdSF$PM25,"<br/>",
    sep="") %>%
lapply(htmltools::HTML)

m = leaflet() %>%
  addProviderTiles("CartoDB.Positron") %>%
  setView(-122.3978, 37.7658, zoom = 12) %>% 
  addPolygons(data = baaqmdSF , 
              fillColor = ~pal(baaqmdSF$PM25), 
              fillOpacity = 0.7, 
              weight = 0.2, 
              smoothFactor = 0.2,
              label = mytext,
              highlight = highlightOptions(
                weight = 5,
                color = "#666",
                fillOpacity = 0.7,
                bringToFront = TRUE),
              popup = ~popup_sb) %>%
  addLegend(pal = pal, 
            values = baaqmdSF$PM25, 
            position = "bottomright", 
            title = "PM2.5 (µg/m³)")

# * Uncomment
htmlwidgets::saveWidget(m, "m.html")
# * Uncomment
rawHTML = base64enc::dataURI(mime = "text/html;charset=utf-8", file = "m.html")
display_html(paste("<iframe src=", rawHTML, "width=100% height=450></iframe>", sep = "\""))
unlink("m.html")

### Hexbin Map

1) https://andrewpwheeler.com/2019/08/07/making-a-hexbin-map-in-ggplot/

2) https://www.r-graph-gallery.com/328-hexbin-map-of-the-usa.html

3) https://atlan.com/courses/introduction-to-gis-r/lesson4-animated-interactive-maps/

4) https://rpubs.com/dieghernan/beautifulmaps_I

5) https://rpubs.com/cengel248/97543

With ggplot (static)

1) https://rud.is/b/2015/05/15/u-s-drought-monitoring-with-hexbin-state-maps-in-r/

2) https://www.data-to-viz.com/graph/hexbinmap.html

3) https://www.r-bloggers.com/geojson-hexagonal-statebins-in-r/

Python

1) https://github.com/UsabilityEtc/d3-geo-hexbin

D3

1) https://observablehq.com/@d3/hexbin-map

2) http://bl.ocks.org/bumbeishvili/60242929b6fef26f7aa54655238ae65d

3) https://observablehq.com/@larsvers/making-a-tesselated-hexbin-map#hexPoints

### HeatMap

In [8]:
m = dygraph(purpleAirT) %>%
  dySeries("PM2.5_ATM_ug.m3", label = "PM2.5") %>%
  dyRangeSelector(height = 20)
htmlwidgets::saveWidget(m, "m.html")
rawHTML = base64enc::dataURI(mime = "text/html;charset=utf-8", file = "m.html")
display_html(paste("<iframe src=", rawHTML, "width=100% height=450></iframe>", sep = "\""))
unlink("m.html")

In [19]:
# bins <- c(8.08,8.37,8.54,8.81,9.19, Inf)
# pal <- colorBin("YlOrRd", domain = baaqmdSF$PM25, bins = bins)

# ui = fluidPage(
#     leaflet(data = purpleAir2) %>% 
#     addProviderTiles(providers$CartoDB.Positron) %>%
#     setView(-122.3978, 37.7658, zoom = 12) %>%
#     addHeatmap(lng = ~Longitude, lat = ~Latitude, intensity = ~as.numeric(PM2.5_ATM_ug.m3), blur = 20, max = 0.08, radius = 15) %>% 
#     addMarkers(data = purpleAir2, lat = ~ Latitude, lng = ~ Longitude, clusterOptions = markerClusterOptions(), popup = ~as.character(PM2.5_ATM_ug.m3), label = ~as.character(paste0("Name: ", sep = " ", location))) %>%
#     addGeoJSON(geojson) %>%
#     addMiniMap()
#     )

# server <- function(input, output, session) {

# }

# shinyApp(ui, server)

## Alt viewing option

m = leaflet(data = purpleAir2) %>% 
    addProviderTiles(providers$CartoDB.Positron) %>%
    setView(-122.3978, 37.7658, zoom = 12) %>%
    addHeatmap(lng = ~Longitude, lat = ~Latitude, intensity = ~as.numeric(PM2.5_ATM_ug.m3), blur = 20, max = 0.05, radius = 15) %>% 
    addMiniMap()

# Will save and render on a separate HTML file

# * Uncomment
htmlwidgets::saveWidget(m, "m.html")

# Doesn't save the html assets, but might not display if too data heavy(?)

# * Uncomment
rawHTML = base64enc::dataURI(mime = "text/html;charset=utf-8", file = "m.html")
display_html(paste("<iframe src=", rawHTML, "width=100% height=450></iframe>", sep = "\""))
unlink("m.html")

Useful Refs:

1) https://rpubs.com/bhaskarvk/leaflet-heat

2) https://stackoverflow.com/questions/48179175/change-leaflet-heatmap-options-in-shiny

3) https://rstudio.github.io/dygraphs/

4) https://bookdown.org/robinlovelace/geocompr/adv-map.html#interactive-maps

5) https://rpubs.com/bhaskarvk/leaflet-heat

6) https://carto.com/help/tutorials/understanding-the-time-series-widget/#animated-time-series-widget

7) http://zevross.com/blog/2018/10/02/creating-beautiful-demographic-maps-in-r-with-the-tidycensus-and-tmap-packages/

8) http://apps.socib.es/Leaflet.TimeDimension/examples/example13.html

9) https://stackoverflow.com/questions/36554605/cant-loop-with-rs-leaflet-package-to-produce-multiple-maps/36587525#36587525

10) https://environmentalinformatics-marburg.github.io/mapview/popups/html/popups.html#popupgraph

11) http://boazsobrado.com/blog/2018/02/08/leaflet-timeline-in-r/

12) https://cfss.uchicago.edu/notes/leaflet/

13) Display html in JN: https://stackoverflow.com/questions/46770320/error-html-widgets-cannot-be-represented-in-plain-text

14) https://rstudio.github.io/leaflet/json.html

15) https://www.r-bloggers.com/queensland-road-accidents-mapped-with-shiny-and-leaflet-in-r/

16) https://stackoverflow.com/questions/34940326/how-can-i-use-daterangenput-for-time-series-plot

17) http://boazsobrado.com/blog/2018/02/08/leaflet-timeline-in-r/

18) https://www.bioconductor.org/help/course-materials/2015/CSAMA2015/lab/shiny.html

In [ ]:
###################################################################################################################

In [ ]:
## Ui Code

ui <- fluidPage(
  mainPanel( 
#this will create a space for us to display our map
leafletOutput(outputId = "mymap"), 
#this allows me to put the checkmarks ontop of the map to allow people to view earthquake depth or overlay a heatmap
absolutePanel(top = 60, left = 20, 
      checkboxInput("markers", "Location", FALSE),
      checkboxInput("heat", "Heatmap", FALSE)
    )
))

In [ ]:
## Server code

server <- function(input, output, session) {
#define the color pallate for the magnitidue of the earthquake
#  pal <- colorNumeric(
#     palette = c('purple'),
#     domain = purpleAir)
  
#define the color of for the location of the sensors
#  pal2 <- colorFactor(
#     palette = c('blue', 'yellow', 'red'),
#     domain = data$depth_type # remplace with coords
#   )
  
#create the map
  output$mymap <- renderLeaflet({
    leaflet(data) %>% 
      setView(lng = -122.3978, lat = 37.7658, zoom = 12)  %>% #setting the view over ~ center of North America
      addTiles() %>% 
      addCircles(data = purpleAir2, lat = ~ Latitude, lng = ~ Longitude, weight = 5, popup = ~as.character(location), label = ~as.character(paste0("Name: ", sep = " ", location)), color = 'purple', fillOpacity = 0.5)
  })
  
##next we use the observe function to make the checkboxes dynamic. If you leave this part out you will see that the checkboxes, when clicked on the first time, display our filters...But if you then uncheck them they stay on. So we need to tell the server to update the map when the checkboxes are unchecked.
#   observe({
#     proxy <- leafletProxy("mymap", data = data)
#     proxy %>% clearMarkers()
#     if (input$markers) {
#       proxy %>% addCircleMarkers(stroke = FALSE, color = ~pal2(depth_type), fillOpacity = 0.2,      label = ~as.character(paste0("Magnitude: ", sep = " ", mag))) %>%
#         addLegend("bottomright", pal = pal2, values = data$depth_type,
#                   title = "Depth Type",
#                   opacity = 1)}
#     else {
#       proxy %>% clearMarkers() %>% clearControls()
#     }
#   })
  
#   observe({
#     proxy <- leafletProxy("mymap", data = data)
#     proxy %>% clearMarkers()
#     if (input$heat) {
#       proxy %>%  addHeatmap(lng=~longitude, lat=~latitude, intensity = ~mag, blur =  10, max = 0.05, radius = 15) 
#       }
#     else{
#       proxy %>% clearHeatmap()
#       }
    
    
#   })
  
}

In [ ]:
shinyApp(ui, server)

In [ ]:
pal = colorNumeric("RdYlBu", domain = purpleAir2$PM2.5_ATM_ug.m3)

m = leaflet(data = purpleAir2) %>% 
  addProviderTiles(providers$CartoDB.Positron) %>% 
  addCircles(col = ~pal(PM2.5_ATM_ug.m3), opacity = 0.9) %>% 
  addLegend(pal = pal, values = ~PM2.5_ATM_ug.m3) %>% 
  setView(lng = -122.3978, 37.7658, zoom = 12) %>% 
  addMiniMap()

## Will save and render on a separate HTML file

htmlwidgets::saveWidget(m, "m.html")
# display_html('<iframe src="m.html" width=100% height=450></iframe>')

## Doesn't save the html assets, but might not display if too data heavy(?)
rawHTML = base64enc::dataURI(mime = "text/html;charset=utf-8", file = "m.html")
display_html(paste("<iframe src=", rawHTML, "width=100% height=450></iframe>", sep = "\""))
unlink("m.html")

# Display html in JN: https://stackoverflow.com/questions/46770320/error-html-widgets-cannot-be-represented-in-plain-text